<img style = "float: left" src="https://mirrors.creativecommons.org/presskit/buttons/88x31/png/by-nc-nd.png" width="120"> &copy; 2024-2025 Roger Villemaire, [villemaire.roger@uqam.ca](mailto:villemaire.roger@uqam.ca)  
[Creative Commons Paternité - Pas d'Utilisation Commerciale - Pas de Modification 3.0 non transcrit](http://creativecommons.org/licenses/by-nc-nd/3.0/)

# SPARQL *SPARQL Protocol and RDF Query Language*

Un programme informatique va normalement accéder à des données, les traiter et en produire de nouvelles. Il s'agit bien sûr de toute cette idée de *traitement de l'information* !

Nous avons déjà vu comment échanger des données entre des fichiers *CSV* et *Excel* et l'environnement Python. Nous allons maintenant considérer les données disponibles sur *Wikidata* qui regroupe des données structurées, utilisées par les différents produits de la fondation Wikimedia, comme Wikipedia, Wikivoyage, Wiktionary, Wikisource, mais aussi disponible librement, pour d'autres usages.

En fait, ces données sont disponibles sous la licence [cc0](https://creativecommons.org/publicdomain/zero/1.0/legalcode)
comme expliqué sur [www.wikidata.org](https://www.wikidata.org).  
De façon générale, il s'agit de

"CC0 1.0 universel (CC0 1.0)
Transfert dans le Domaine Public

La personne qui a associé une œuvre à cet acte a dédié l’œuvre au domaine public en renonçant dans le monde entier à ses droits sur l’œuvre selon les lois sur le droit d’auteur, droit voisin et connexes, dans la mesure permise par la loi.

Vous pouvez copier, modifier, distribuer et représenter l’œuvre, même à des fins commerciales, sans avoir besoin de demander l’autorisation."

## Interface web de requêtes

Pour débuter avec cet imposant jeu de données, le plus simple est d'expérimenter avec le moteur de requêtes en version web [query.wikidata.org](https://query.wikidata.org/).  
Notez que Ctrl-espace permet d'obtenir un menu contextuel dans cet outil.

Débutons avec une requête simple pour obtenir toutes les universités situées au Québec.  
Copiez le code SPARQL ci-dessous dans l'interface du moteur de recherche ci-dessus et faites-le exécuter.

On peut toujours ajouter des clauses pour préciser la recherche, comme dans l'exemple suivant.

Bizarrement, l'UQAM ne semble pas administrativement située à Montréal. Mais où est-elle donc ?  
On va tout d'abord localiser l'information au sujet de l'UQAM.

On peut maintenant accéder la page web de l'entité *Q1634522* et trouver le bon prédicat. Ici toutes les relations sont formées de triplets (sujet, prédicat, objet).  
On peut finalement trouver toutes les universités dont le siège principal est à Montréal.

## Requêtes SPARQL en Python

Maintenant que nous sommes un peu plus familiers avec les requêtes SPARQL, nous allons voir qu'on peut faire les mêmes opérations dans un programme Python et
ainsi obtenir des données qu'on pourra traiter et utiliser dans ce langage de programmation. Ce qui est donc très général et puissant.

Tout d'abord, il faut comprendre que wikidata n'offre pas seulement l'interface que nous venons de voir, mais un *point d'accès SPARQL*. Il s'agit d'une URL
à laquelle nous pouvons transmettre une requête SPARQL, comme celle qui apparaissait dans l'interface ci-dessus et obtenir la réponse.

En fait, on pourrait simplement entrer une url comme la suivante, qui contient, en plus de l'adresse du point d'accès SPARQL, la requête elle-même, dans 
notre fureteur et on obtiendrait la réponse sous la forme d'un fichier XML contenant la réponse.

In [ ]:
https://query.wikidata.org/sparql?query=SELECT%20?uqam%20?uqamLabel%20WHERE%20{%20VALUES%20?uqam%20{wd:Q1634522}.%20SERVICE%20wikibase:label%20{%20bd:serviceParam%20wikibase:language%20%22[AUTO_LANGUAGE],en%22.%20}%20}%20LIMIT%20100

Ça ne serait pas très pratique, ni de construire une telle URL ni surtout de devoir analyser le fichier XML contenant bien la réponse voulue, mais dans un format assez complexe. La solution est de bien sûr utiliser une bibliothèque qui traitera de tous ces aspects techniques et nous rendra la vie plus agréable !

Il y a plusieurs choix possibles, nous allons utiliser *sparql-client*. qui semble être encore en activité, de sa page web, et avoir le soutien d'une organisation.

Tout d'abord, dans le navigateur Anaconda, faire Environments -> <environnement courant> 'play' -> 'open terminal'.  
Maintenant, sur la ligne de commande, faites l'installation de la bibliothèque avec  
pip install sparql-client

On peut maintenant importer ce module dans l'environnement Python

In [ ]:
import base64
base64.encodestring = base64.encodebytes
base64.decodestring = base64.decodebytes

In [ ]:
import collections
try:
    from collections import abc
    collections.MutableMapping = abc.MutableMapping
except:
    pass

In [ ]:
import sparql

La démarche est de tout d'abord créer une requête, qui est simplement une chaîne de caractères formant une requête SPARQL.  
*Note :* Remarquez l'usage des triple-guillemets, nécessaires puisque la requête est formée de plusieurs lignes.

In [ ]:
requete = '''SELECT ?uqam ?uqamLabel WHERE {
  VALUES ?uqam {wd:Q1634522}.
  SERVICE wikibase:label { bd:serviceParam wikibase:language "fr,en". } # le label en français de préférence, et autrement en anglais
}'''

En second lieu, on transmet cette requête au point d'accès (endpoint) SPARQL de wikidata (on trouve son URL sur la page [www.wikidata.org/wiki/Wikidata:SPARQL_query_service](https://www.wikidata.org/wiki/Wikidata:SPARQL_query_service)).

In [ ]:
import ssl
ssl._create_default_https_context = ssl._create_unverified_context

In [ ]:
resultat = sparql.query('https://query.wikidata.org/bigdata/namespace/wdq/sparql', requete)

L'exécution peut durer quelques secondes, mais lorsque la réponse est arrivée on peut l'accéder dans la variable *resultat*.

La réponse contient des éléments déterminés par les valeurs des variables demandées. C'est donc similaire à un tableur, comme vu dans le bas de l'interface web de requêtes, vu ci-dessus.

On peut accéder ces variables, qui sont celles de la requête.

In [ ]:
resultat.variables

Le résultat est dans un type de données spécifique à sparql-client.

In [ ]:
type(resultat)

On peut maintenant extraire les éléments un par un, où plus simplement tous les obtenir d'un seul coup sous la forme d'une liste. Il s'agit bien sûr d'une liste Python, et comme n'importe quelle autre et on peut à partir de là traiter les données avec du code Python.

*Attention* : Après l'exécution de 'fetchall' la variable 'resultat' est vide et peut être réutilisée pour une autre requête.

In [ ]:
elements = resultat.fetchall()

In [ ]:
elements

Il faut maintenant décomposer cette valeur. On débute en faisant l'extraction de l'unique élément de la liste.

In [ ]:
[element] = elements

In [ ]:
element

In [ ]:
type(element)

In [ ]:
len(element)

On peut maintenant extraire les deux composantes du couple.

In [ ]:
(iri,literal) = element

In [ ]:
iri

In [ ]:
type(iri)

In [ ]:
iri.value

In [ ]:
literal

In [ ]:
type(literal)

In [ ]:
literal.lang

In [ ]:
literal.value

In [ ]:
"\u00e9"

## Exercices

1. Dans l'interface [query.wikidata.org](https://query.wikidata.org/) complétez la partie qui suit *wdt:* ci-dessous pour former une requête SPARQL qui retournera le *pays* dans lequel l'UQAM est située !

2. Utilisez maintenant votre requête pour, à l'aide de sparql-client comme ci-dessus, compléter les instructions ci-dessous pour obtenir le nom de ce pays sous la forme d'une chaîne de caractères Python.

In [ ]:
requete = 

In [ ]:
resultat = sparql.query('https://query.wikidata.org/bigdata/namespace/wdq/sparql', requete)

In [ ]:
elements = resultat.fetchall()

**S'il vous reste du temps, vous pouvez travailler sur les exercices suivants.**

3. Dans l'interface [query.wikidata.org](https://query.wikidata.org/) concevez une requête SPARQL pour obtenir en plus du pays, la *nature de l'élément* (instance of) de l'UQAM.

4. Utilisez maintenant votre requête pour, à l'aide de sparql-client comme ci-dessus, obtenir le nom du pays ainsi que la nature sous la forme de chaînes de caractères Python.

5. Concevez maintenant une requête pour trouver toutes les intitutions de même nature que l'UQAM dans le même pays que l'UQAM. Observez bien les résultats obtenus dans l'interface  [query.wikidata.org](https://query.wikidata.org/).

6. Vous pouvez aussi écrire le code Python nécessaire pour obtenir le nombre d'éléments retournés par la requête précédente.